In [123]:
# Download pandas-profiling
! pip install [https://github.com/pandas-profiling/pandas-profiling/archive/master.zip](https://github.com/pandas-profiling/pandas-profiling/archive/master.zip)
! pip install plotly==5.13.0
!pip install pandas-profiling
! pip install https://github.com/pandas-profiling/pandas-profiling/archive/master.zip
!pip install ipywidgets

/bin/bash: -c: line 1: syntax error near unexpected token `('
/bin/bash: -c: line 1: ` pip install [https://github.com/pandas-profiling/pandas-profiling/archive/master.zip](https://github.com/pandas-profiling/pandas-profiling/archive/master.zip)'
  Using cached https://github.com/pandas-profiling/pandas-profiling/archive/master.zip
  Preparing metadata (setup.py) ... done


In [255]:
import pickle
import numpy as np
import pandas as pd
from sklearn.svm import SVC
from sklearn.neighbors import KNeighborsClassifier
from xgboost import XGBClassifier
from pandas_profiling import ProfileReport
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import accuracy_score, confusion_matrix, classification_report

In [256]:
data = pd.read_csv('/content/titanic-passengers.csv', sep=';')
data

PassengerId Survived  Pclass  \
0            343       No       2   
1             76       No       3   
2            641       No       3   
3            568       No       3   
4            672       No       1   
..           ...      ...     ...   
886           10      Yes       2   
887           61       No       3   
888          535       No       3   
889          102       No       3   
890          428      Yes       2   

                                                  Name     Sex   Age  SibSp  \
0                           Collander, Mr. Erik Gustaf    male  28.0      0   
1                              Moen, Mr. Sigurd Hansen    male  25.0      0   
2                               Jensen, Mr. Hans Peder    male  20.0      0   
3          Palsson, Mrs. Nils (Alma Cornelia Berglund)  female  29.0      0   
4                               Davidson, Mr. Thornton    male  31.0      1   
..                                                 ...     ...   ...    ...   
886                Nasser, Mrs. Nicholas (Adele Achem)  female  14.0      1   
887                              Sirayanian, Mr. Orsen    male  22.0      0   
888                                Cacic, Miss. Marija  female  30.0      0   
889                   Petroff, Mr. Pastcho ("Pentcho")    male   NaN      0   
890  Phillips, Miss. Kate Florence ("Mrs Kate Louis...  female  19.0      0   

     Parch      Ticket     Fare  Cabin Embarked  
0        0      248740  13.0000    NaN        S  
1        0      348123   7.6500  F G73        S  
2        0      350050   7.8542    NaN        S  
3        4      349909  21.0750    NaN        S  
4        0  F.C. 12750  52.0000    B71        S  
..     ...         ...      ...    ...      ...  
886      0      237736  30.0708    NaN        C  
887      0        2669   7.2292    NaN        C  
888      0      315084   8.6625    NaN        S  
889      0      349215   7.8958    NaN        S  
890      0      250655  26.0000    NaN        S  

[891 rows x 12 columns]

In [165]:
# all the details about the data
details = ProfileReport(data)
details.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [257]:
# We will remove the unique features and the useless one
features_remove = ['PassengerId', 'Name', 'Ticket', 'Cabin']
data = data.drop(features_remove, axis=1)
data

Survived  Pclass     Sex   Age  SibSp  Parch     Fare Embarked
0         No       2    male  28.0      0      0  13.0000        S
1         No       3    male  25.0      0      0   7.6500        S
2         No       3    male  20.0      0      0   7.8542        S
3         No       3  female  29.0      0      4  21.0750        S
4         No       1    male  31.0      1      0  52.0000        S
..       ...     ...     ...   ...    ...    ...      ...      ...
886      Yes       2  female  14.0      1      0  30.0708        C
887       No       3    male  22.0      0      0   7.2292        C
888       No       3  female  30.0      0      0   8.6625        S
889       No       3    male   NaN      0      0   7.8958        S
890      Yes       2  female  19.0      0      0  26.0000        S

[891 rows x 8 columns]

In [258]:
# Removing Outliers
def remove_outliers(data, column):
  Q1 = data[column].quantile(0.25)
  Q3 = data[column].quantile(0.75)
  IQR = Q3 - Q1

  lower_bound = Q1 - 1.5 * IQR
  upper_bound = Q3 + 1.5 * IQR

  data = data[(data[column] >= lower_bound) & (data[column] <= upper_bound)]
  return data

outliers_col = ['Fare', 'Age', 'SibSp', 'Pclass']

for i in outliers_col:
  data = remove_outliers(data, i)

data

Survived  Pclass     Sex   Age  SibSp  Parch     Fare Embarked
0         No       2    male  28.0      0      0  13.0000        S
1         No       3    male  25.0      0      0   7.6500        S
2         No       3    male  20.0      0      0   7.8542        S
3         No       3  female  29.0      0      4  21.0750        S
4         No       1    male  31.0      1      0  52.0000        S
..       ...     ...     ...   ...    ...    ...      ...      ...
885       No       2    male  42.0      0      0  13.0000        S
886      Yes       2  female  14.0      1      0  30.0708        C
887       No       3    male  22.0      0      0   7.2292        C
888       No       3  female  30.0      0      0   8.6625        S
890      Yes       2  female  19.0      0      0  26.0000        S

[569 rows x 8 columns]

In [259]:
# Fill age missing value
data['Age'].fillna(data['Age'].mean(), inplace=True)
data['Age'].isnull().sum()

0

In [260]:
# Change the strings to nums in Survived and Embarked
val = {'Survived' : {'Yes' : 1, 'No' : 0}, 'Embarked' : {'S' : 0, 'C' : 1, 'Q' : 2}, 'Sex' : {'male' : 0 , 'female' : 1}}
data.replace(val, inplace=True)

In [261]:
# all the details about the data
details = ProfileReport(data)
details.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

In [262]:
data.drop_duplicates(inplace=True)
data

Survived  Pclass  Sex   Age  SibSp  Parch     Fare  Embarked
0           0       2    0  28.0      0      0  13.0000         0
1           0       3    0  25.0      0      0   7.6500         0
2           0       3    0  20.0      0      0   7.8542         0
3           0       3    1  29.0      0      4  21.0750         0
4           0       1    0  31.0      1      0  52.0000         0
..        ...     ...  ...   ...    ...    ...      ...       ...
885         0       2    0  42.0      0      0  13.0000         0
886         1       2    1  14.0      1      0  30.0708         1
887         0       3    0  22.0      0      0   7.2292         1
888         0       3    1  30.0      0      0   8.6625         0
890         1       2    1  19.0      0      0  26.0000         0

[532 rows x 8 columns]

In [264]:
# Separate data
y = data['Survived']
y

0      0
1      0
2      0
3      0
4      0
      ..
885    0
886    1
887    0
888    0
890    1
Name: Survived, Length: 532, dtype: int64

In [265]:
x = data.drop(['Survived'], axis=1)
x

Pclass  Sex   Age  SibSp  Parch     Fare  Embarked
0         2    0  28.0      0      0  13.0000         0
1         3    0  25.0      0      0   7.6500         0
2         3    0  20.0      0      0   7.8542         0
3         3    1  29.0      0      4  21.0750         0
4         1    0  31.0      1      0  52.0000         0
..      ...  ...   ...    ...    ...      ...       ...
885       2    0  42.0      0      0  13.0000         0
886       2    1  14.0      1      0  30.0708         1
887       3    0  22.0      0      0   7.2292         1
888       3    1  30.0      0      0   8.6625         0
890       2    1  19.0      0      0  26.0000         0

[532 rows x 7 columns]

Pclass  Sex   Age  SibSp  Parch     Fare  Embarked
0         2    0  28.0      0      0  13.0000         0
1         3    0  25.0      0      0   7.6500         0
2         3    0  20.0      0      0   7.8542         0
3         3    1  29.0      0      4  21.0750         0
4         1    0  31.0      1      0  52.0000         0
..      ...  ...   ...    ...    ...      ...       ...
885       2    0  42.0      0      0  13.0000         0
886       2    1  14.0      1      0  30.0708         1
887       3    0  22.0      0      0   7.2292         1
888       3    1  30.0      0      0   8.6625         0
890       2    1  19.0      0      0  26.0000         0

[532 rows x 7 columns]

In [267]:
from imblearn.over_sampling import SMOTE
from sklearn.datasets import make_classification

x, y = make_classification(n_samples=1000, n_features=8, n_informative=6,
                           n_redundant=2, n_clusters_per_class=1,
                           weights=[0.1, 0.9], flip_y=0, random_state=42)

In [268]:
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.2, random_state=42)

In [269]:
# Logisitic Regression
model = LogisticRegression()
model.fit(x_train, y_train)

LogisticRegression()

In [270]:
model.score(x_test,y_test)

0.93

In [271]:
# SVC
model_2 = SVC()
model_2.fit(x_train, y_train)

SVC()

In [272]:
model_2.score(x_test,y_test)

0.955

In [273]:
# KNN
acc = 0
for i in range(1,10):
  model_3 = KNeighborsClassifier(n_neighbors=i)
  model_3.fit(x_train, y_train)
  acc = max(acc, model_3.score(x_test,y_test))
acc

0.965

In [274]:
model_3.score(x_test,y_test)

0.955

In [275]:
# XGclassifier
model_4 = XGBClassifier()
model_4.fit(x_train, y_train)

XGBClassifier(base_score=None, booster=None, callbacks=None,
              colsample_bylevel=None, colsample_bynode=None,
              colsample_bytree=None, device=None, early_stopping_rounds=None,
              enable_categorical=False, eval_metric=None, feature_types=None,
              gamma=None, grow_policy=None, importance_type=None,
              interaction_constraints=None, learning_rate=None, max_bin=None,
              max_cat_threshold=None, max_cat_to_onehot=None,
              max_delta_step=None, max_depth=None, max_leaves=None,
              min_child_weight=None, missing=nan, monotone_constraints=None,
              multi_strategy=None, n_estimators=None, n_jobs=None,
              num_parallel_tree=None, random_state=None, ...)

In [276]:
model_4.score(x_test,y_test)

0.98

In [277]:
# Save Model
pickle.dump(model_4, open('model.sav', 'wb'))